# How Electric Generation Infrastructure and Fuel Diversity Influence Frid Resilience Across U.S. States
**Name(s)**: Jiaying Chen, Minh Hoang

**Website Link**: [How Electric Generation Infrastructure and Fuel Diversity Influence Frid Resilience Across U.S. States](https://rcwoshimao.github.io/infrastructure-resilience-analysis/)


**Note**: Run this command to install wordcloud:
`!pip install wordcloud`

In [1]:
!pip install wordcloud

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from pathlib import Path
from wordcloud import WordCloud


import plotly.express as px
import plotly.graph_objects as go

#newly added
from scipy.stats import permutation_test #easy permutation testing
from itertools import combinations
from pandas.api.types import is_numeric_dtype
#model business
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
from sklearn.ensemble import RandomForestRegressor
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import RandomizedSearchCV
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import r2_score


pd.options.plotting.backend = 'plotly'

# from dsc80_utils import * # Feel free to uncomment and use this.

# Step 1: Introduction

### Loading data

In [2]:

raw = pd.read_csv('outage.csv', header=None).iloc[5:]
cols = raw.iloc[0, 1:].tolist()
raw = raw.iloc[1:, 1:].copy()
raw.columns = cols
raw.reset_index(drop=True, inplace=True)
raw = raw.iloc[1:, :]
raw.head(2)

OBS  YEAR MONTH U.S._STATE POSTAL.CODE NERC.REGION      CLIMATE.REGION  \
1   1  2011     7  Minnesota          MN         MRO  East North Central   
2   2  2014     5  Minnesota          MN         MRO  East North Central   

  ANOMALY.LEVEL CLIMATE.CATEGORY     OUTAGE.START.DATE  ... POPPCT_URBAN  \
1          -0.3           normal  Friday, July 1, 2011  ...        73.27   
2          -0.1           normal  Sunday, May 11, 2014  ...        73.27   

  POPPCT_UC POPDEN_URBAN POPDEN_UC POPDEN_RURAL AREAPCT_URBAN AREAPCT_UC  \
1     15.28         2279    1700.5         18.2          2.14        0.6   
2     15.28         2279    1700.5         18.2          2.14        0.6   

           PCT_LAND     PCT_WATER_TOT  PCT_WATER_INLAND  
1  91.5926658691451  8.40733413085488  5.47874298334407  
2  91.5926658691451  8.40733413085488  5.47874298334407  

[2 rows x 56 columns]

### Renaming columns

In [3]:
new_cols = [
    'obs', 'year', 'month', 'state', 'postal_code', 'nerc_region',
    'climate_region', 'anomaly_level', 'climate_cat',
    'start_date', 'start_time', 'restore_date',
    'restore_time', 'cause_cat', 'cause_detail',
    'hurricane_names', 'duration', 'demand_loss_mw',
    'customers_affected', 'res_price', 'com_price', 'ind_price',
    'total_price', 'res_sales', 'com_sales', 'ind_sales', 'total_sales',
    'res_pct', 'com_pct', 'ind_pct', 'res_customers',
    'com_customers', 'ind_customers', 'total_customers', 'res_cust_pct',
    'com_cust_pct', 'ind_cust_pct', 'pc_realgsp_state', 'pc_realgsp_usa',
    'pc_realgsp_rel', 'pc_realgsp_change', 'util_realgsp', 'total_realgsp',
    'util_contri', 'pi_util_of_usa', 'population', 'pop_pct_urban',
    'pop_pct_uc', 'popden_urban', 'popden_uc', 'popden_rural',
    'area_pct_urban', 'area_pct_uc', 'pct_land', 'pct_water_tot',
    'pct_water_inland'
]

raw.columns = new_cols
raw.head(2)


obs  year month      state postal_code nerc_region      climate_region  \
1   1  2011     7  Minnesota          MN         MRO  East North Central   
2   2  2014     5  Minnesota          MN         MRO  East North Central   

  anomaly_level climate_cat            start_date  ... pop_pct_urban  \
1          -0.3      normal  Friday, July 1, 2011  ...         73.27   
2          -0.1      normal  Sunday, May 11, 2014  ...         73.27   

  pop_pct_uc popden_urban popden_uc popden_rural area_pct_urban area_pct_uc  \
1      15.28         2279    1700.5         18.2           2.14         0.6   
2      15.28         2279    1700.5         18.2           2.14         0.6   

           pct_land     pct_water_tot  pct_water_inland  
1  91.5926658691451  8.40733413085488  5.47874298334407  
2  91.5926658691451  8.40733413085488  5.47874298334407  

[2 rows x 56 columns]

In [4]:
raw.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1534 entries, 1 to 1534
Data columns (total 56 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   obs                 1534 non-null   object
 1   year                1534 non-null   object
 2   month               1525 non-null   object
 3   state               1534 non-null   object
 4   postal_code         1534 non-null   object
 5   nerc_region         1534 non-null   object
 6   climate_region      1528 non-null   object
 7   anomaly_level       1525 non-null   object
 8   climate_cat         1525 non-null   object
 9   start_date          1525 non-null   object
 10  start_time          1525 non-null   object
 11  restore_date        1476 non-null   object
 12  restore_time        1476 non-null   object
 13  cause_cat           1534 non-null   object
 14  cause_detail        1063 non-null   object
 15  hurricane_names     72 non-null     object
 16  duration            1476

## Introduction and Question Identification
(⚠️ means still need more data, ✅ means workable with existing data )

**Currently, we are considering three problem statement to explore:**

1. ⚠️ Assessment of Infrastructure Resilience (Based on whether or not `cause_detail` has enough information.)
Analyze how different regions' infrastructure characteristics (e.g., overhead vs. underground lines, maintenance investments) correlate with outage frequency and duration. This can inform infrastructure improvement strategies.
2. ✅ Temporal Trends and Climate Change Correlation (doable with existing data, but kinda boring) 
Examine how the frequency and causes of outages have evolved over time and assess potential correlations with climate change indicators. This can provide insights into how changing climate patterns impact power reliability.
3. ⚠️ Policy and Emergency Response Evaluation (We don’t have explicit timestamps or markers indicating policy changes or emergency response dates.)
Evaluate the effectiveness of policies and emergency responses by analyzing outage data before and after the implementation of specific measures. This can guide future policy development and emergency planning.

**Ideas that are just "ok":**

⭕️ 1. Predictive Modeling of Outage Risks <u> ***(but it’s kinda boring, i bet people have done it already; not creative)*** </u>

Utilize machine learning techniques to predict the likelihood of major power outages based on factors such as weather patterns, infrastructure characteristics, and economic indicators. This can aid in proactive maintenance and resource allocation.

⭕️ 2. Socioeconomic Impact Analysis <u> ***(has been done numerous times already !!!!!!! Check out examples, two of them already exist. I know you like it, Im sry!)*** </u>

Investigate the relationship between socioeconomic factors (e.g., income levels, urbanization) and the frequency or duration of power outages. This can highlight areas where outages disproportionately affect vulnerable populations.



### Exploring idea 1
Check out whether `cause_detail` gives us any good information about the infrustructure. 

In [5]:
raw['cause_detail'].unique()

array([nan, 'vandalism', 'heavy wind', 'thunderstorm', 'winter storm',
       'tornadoes', 'sabotage', 'hailstorm', 'uncontrolled loss',
       'winter', 'wind storm', 'computer hardware', 'public appeal',
       'storm', ' Coal', ' Natural Gas', 'hurricanes', 'wind/rain',
       'snow/ice storm', 'snow/ice ', 'transmission interruption',
       'flooding', 'transformer outage', 'generator trip',
       'relaying malfunction', 'transmission trip', 'lightning',
       'switching', 'shed load', 'line fault', 'breaker trip', 'wildfire',
       ' Hydro', 'majorsystem interruption', 'voltage reduction',
       'transmission', 'Coal', 'substation', 'heatwave',
       'distribution interruption', 'wind', 'suspicious activity',
       'feeder shutdown', '100 MW loadshed', 'plant trip', 'fog', 'Hydro',
       'earthquake', 'HVSubstation interruption', 'cables', 'Petroleum',
       'thunderstorm; islanding', 'failure'], dtype=object)

- `cause_detail` does contain some infrastructure-related failure types, like:
**transformer outage, generator trip, relaying malfunction, breaker trip, line fault, substation, transmission interruption, distribution interruption, cables, HVSubstation interruption, plant trip**, etc.
- They will allow us to indirectly infer infrastructure issues, but there are no explicit infrastructure metadata: We don’t have direct info on overhead vs underground lines, age of equipment, maintenance budgets, or investments.

- External datasets to consider: 
    - **(I FW THIS ONE HEAVY) [EIA Reports on Utility Investments](https://www.eia.gov/todayinenergy/detail.php?id=48136)** 
        - Provides financial and operational data related to maintenance and upgrades.
        - Can help explain or correlate investment levels with outage frequency/duration.
        - Good source for explaining patterns seen in outage data.
    - [Mapping the Depths: Underground Power Distribution (arXiv study, paper only)](https://arxiv.org/abs/2402.06668)
        - Unique dataset that quantifies underground vs overhead lines by utility.
        - Can provide a strong predictor variable about infrastructure type (underground = more resilient).

### Exploring EIA reports on utility investment 
-> <u> **[Annual Electric Power Industry Report, Form EIA-861 detailed data files](https://www.eia.gov/electricity/data/eia861/)**</u> <br>
-> <u> **[A Guide to EIA Electric Power Data](https://www.eia.gov/electricity/data/guide/pdf/guide.pdf)** page 9/18  </u> 
> **Retail Sales by Electric Utilities and Power Marketers (Form EIA-861, Annual Electric Power Industry Report)**
>
> Data Collected by Form EIA-861  
> The Form EIA-861, Annual Electric Power Industry Report collects annual data from a census of all utilities that sell electricity to end-use customers in the 50 states, the District of Columbia, Puerto Rico, American Samoa, the American Virgin Islands, Guam, and the Northern Mariana Islands. These surveys collect information on sales to ultimate customers by utilities and power marketers, energy efficiency programs, distributed generating capacity, and related data elements.  
>
> The data collected include several items:  
> - **Service territory by state and county**  
> - **Sales revenue to ultimate customers**  
> - **Revenue and customer count**  
> - **Source and disposition of electricity**  
> - **Advanced metering**  
> - **Demand response and energy efficiency programs**  
> - **Dynamic pricing**  
> - **Capacity and other information related to net metering**  
> - **Non-net metered distributed generating units**  
> - **Distribution system characteristics and reliability**


Out of the above, the good columns to look for are ` Distribution System Characteristics and Reliability`, ` Service Territory by State and County`, `Advanced Metering Infrastructure (AMI)`, `Revenue and Customer Count by Utility` 
-  `Distribution System Characteristics and Reliability`: Directly speaks to infrastructure resilience. 
-  `Service Territory by State and County`: Needed for merging 
- `Advanced Metering Infrastructure (AMI)`: AMI often correlates with modernization efforts and may reflect better outage response times. Can assess: Compare outage duration/frequency in regions with vs. without AMI.
- `Demand Response and Energy Efficiency Programs`: May suggest proactive infrastructure investment or mitigation strategies. Can assess: "Do regions with stronger demand response programs show fewer or shorter outages?"
- `Revenue and Customer Count by Utility`: Can assess possible correlations between revenue and investment in resilience.

### Setback and change of problem statement
However, later on into the project, we realized there are no good data sources for tracking state investment to power utilities. The form EIA 861 provides data that are already innate to the given outage dataframe.   
But we still want to focus on interesting supply side data, since demand-side data in the given dataframe has likely already been exploited and explored by many. Thus, we shifted our focus onto the operation and generation of electrical power supply instead of investment.  
We inspected **[other forms provided by EIA](https://www.eia.gov/electricity/data/state/)**, and two of we found interesting are the [EIA-860 Annual Electric Generator Report](https://www.eia.gov/electricity/data/eia860/), and the [EIA-923 Power Plant Operations Report](https://www.eia.gov/electricity/data/eia923/). At last, we came up with our final problem statement as below:




# How Electric Generation Infrastructure and Fuel Diversity Influence Grid Resilience Across U.S. States

Motivation:
While customer demand, pricing, and regional weather events are commonly studied in power outage analysis, much less attention is paid to how the supply-side characteristics of a state's power grid—including generation capacity, fuel mix, and generator diversity—contribute to its resilience. A robust grid isn't just about weather-proofing—it may also reflect investments in flexible infrastructure, diversified energy sources, and state-level energy planning.

Project Objective:
We investigate the relationship between generation capacity, fuel source diversity, and actual electricity generation (via EIA-860 and EIA-923) with outage frequency, duration, and impact (via DOE outage data).
We aim to answer:

Do states with more diverse energy portfolios experience fewer or shorter outages?

Does a higher capacity-to-population ratio correlate with better grid performance?

Are certain fuel sources (e.g., natural gas, renewables) associated with better resilience during high-demand or extreme weather years?



# Step 2: Data Cleaning and Exploratory Data Analysis

In [6]:
raw.head(2)

obs  year month      state postal_code nerc_region      climate_region  \
1   1  2011     7  Minnesota          MN         MRO  East North Central   
2   2  2014     5  Minnesota          MN         MRO  East North Central   

  anomaly_level climate_cat            start_date  ... pop_pct_urban  \
1          -0.3      normal  Friday, July 1, 2011  ...         73.27   
2          -0.1      normal  Sunday, May 11, 2014  ...         73.27   

  pop_pct_uc popden_urban popden_uc popden_rural area_pct_urban area_pct_uc  \
1      15.28         2279    1700.5         18.2           2.14         0.6   
2      15.28         2279    1700.5         18.2           2.14         0.6   

           pct_land     pct_water_tot  pct_water_inland  
1  91.5926658691451  8.40733413085488  5.47874298334407  
2  91.5926658691451  8.40733413085488  5.47874298334407  

[2 rows x 56 columns]

## Data cleaning for main dataframe: outages

### Dropping unused features

Since we will be focusing on assessing infrastructure resilience by state based on investment and other economic factors, we have dropped many climate or sales related columns. 

In [7]:
dropped = [
    'obs', 'start_date', 'start_time', 'restore_date', 'restore_time',
    'res_price', 'com_price', 'ind_price',
    'res_sales', 'com_sales', 'ind_sales',
    'res_pct', 'com_pct', 'ind_pct',
    'res_customers', 'com_customers', 'ind_customers',
    'res_cust_pct', 'com_cust_pct', 'ind_cust_pct',
    'pct_land', 'pct_water_tot', 'pct_water_inland',
    'hurricane_names', 'state', 'pc_realgsp_usa', 
    'pc_realgsp_rel', 'pc_realgsp_change', 'util_realgsp',
    'total_realgsp', 'util_contri', 'nerc_region',
    'demand_loss_mw', 'customers_affected',
    'total_price', 'total_sales', 'total_customers',#  'month'
]
raw_dropped = raw.drop(columns = dropped)
raw_dropped = raw_dropped.rename(columns = {'postal_code': 'state'})

# Dropping individual NaNs: first convert all string NaN into np, then drop accordingly. 
raw_dropped = raw_dropped.replace("NaN", np.nan)
raw_dropped = raw_dropped.dropna(subset=['year', 'state']) 
raw_dropped.head(2)

year month state      climate_region anomaly_level climate_cat  \
1  2011     7    MN  East North Central          -0.3      normal   
2  2014     5    MN  East North Central          -0.1      normal   

            cause_cat cause_detail duration pc_realgsp_state pi_util_of_usa  \
1      severe weather          NaN     3060            51268            2.2   
2  intentional attack    vandalism        1            53499            2.2   

  population pop_pct_urban pop_pct_uc popden_urban popden_uc popden_rural  \
1    5348119         73.27      15.28         2279    1700.5         18.2   
2    5457125         73.27      15.28         2279    1700.5         18.2   

  area_pct_urban area_pct_uc  
1           2.14         0.6  
2           2.14         0.6

### Feature enrgineering

In [8]:
# Make duration numeric, standardize cause_detail text 
raw_dropped['duration'] = pd.to_numeric(raw_dropped['duration'], errors='coerce')
raw_dropped['cause_detail'] = raw_dropped['cause_detail'].dropna().astype(str).str.lower().str.strip().str.replace(r'[^\w\s]', '', regex=True).str.replace(r'\s+', ' ', regex=True)


"""
New columns for: 
Total outages that year in that state
Average outage duration that year in that state
"""
outages_count = (raw_dropped.groupby(['year', 'state']).size().reset_index(name='yearly_outage_count_bystate'))
avg_duration = (raw_dropped.groupby(['year', 'state'])['duration'].mean().reset_index(name='yearly_avg_duration_bystate'))
by_year = pd.merge(outages_count, avg_duration, on = ['year', 'state'], how = 'outer')
outage = pd.merge(raw_dropped, by_year, on = ['year', 'state'], how = 'left')
outage.head(2)

year month state      climate_region anomaly_level climate_cat  \
0  2011     7    MN  East North Central          -0.3      normal   
1  2014     5    MN  East North Central          -0.1      normal   

            cause_cat cause_detail  duration pc_realgsp_state  ... population  \
0      severe weather          NaN    3060.0            51268  ...    5348119   
1  intentional attack    vandalism       1.0            53499  ...    5457125   

  pop_pct_urban pop_pct_uc popden_urban popden_uc popden_rural area_pct_urban  \
0         73.27      15.28         2279    1700.5         18.2           2.14   
1         73.27      15.28         2279    1700.5         18.2           2.14   

  area_pct_uc yearly_outage_count_bystate  yearly_avg_duration_bystate  
0         0.6                           3                  1460.666667  
1         0.6                           2                    30.500000  

[2 rows x 21 columns]

In [9]:
# Convert all numeric and categorical column types here 
numerics = ['duration', 'population', 'pop_pct_urban', 'pop_pct_uc', 'popden_urban', 'popden_uc', 'popden_rural', 'area_pct_urban', 'area_pct_uc', 'pi_util_of_usa', 'pc_realgsp_state']
for col in numerics:
    outage[col] = pd.to_numeric(outage[col])
outage.dtypes
categorical = ['year', 'state', 'climate_region', 'cause_cat', 'anomaly_level', 'climate_cat', 'cause_detail']
for col in categorical:
    outage[col] = pd.Categorical(outage[col])

In [10]:
outage.head()

year month state      climate_region anomaly_level climate_cat  \
0  2011     7    MN  East North Central          -0.3      normal   
1  2014     5    MN  East North Central          -0.1      normal   
2  2010    10    MN  East North Central          -1.5        cold   
3  2012     6    MN  East North Central          -0.1      normal   
4  2015     7    MN  East North Central           1.2        warm   

            cause_cat  cause_detail  duration  pc_realgsp_state  ...  \
0      severe weather           NaN    3060.0             51268  ...   
1  intentional attack     vandalism       1.0             53499  ...   
2      severe weather    heavy wind    3000.0             50447  ...   
3      severe weather  thunderstorm    2550.0             51598  ...   
4      severe weather           NaN    1740.0             54431  ...   

   population  pop_pct_urban  pop_pct_uc  popden_urban  popden_uc  \
0     5348119          73.27       15.28        2279.0     1700.5   
1     5457125          73.27       15.28        2279.0     1700.5   
2     5310903          73.27       15.28        2279.0     1700.5   
3     5380443          73.27       15.28        2279.0     1700.5   
4     5489594          73.27       15.28        2279.0     1700.5   

   popden_rural  area_pct_urban  area_pct_uc  yearly_outage_count_bystate  \
0          18.2            2.14          0.6                            3   
1          18.2            2.14          0.6                            2   
2          18.2            2.14          0.6                            3   
3          18.2            2.14          0.6                            1   
4          18.2            2.14          0.6                            2   

   yearly_avg_duration_bystate  
0                  1460.666667  
1                    30.500000  
2                  2610.000000  
3                  2550.000000  
4                   947.500000  

[5 rows x 21 columns]

## Data cleaning and feature engineering: capacity and generation

We cleaned and filtered the capacity and generation datasets to include only state-level records from 2000 to 2016. For both datasets, we renamed columns for clarity, removed commas from numeric fields, and converted values to appropriate data types. In the capacity data, we kept only rows where the fuel source was 'All Sources', while in the generation data, we dropped rows with missing values and excluded entries labeled 'Total' under fuel source. We also converted the year column to string in both datasets to ensure consistency during grouping.

We were originally going to using capacity per capita, but this didnt work because there are too many missing population values in state-year population pairs. After doing some research, we decided to engineer the features `capacity_fuel_diversity_index` and `generation_fuel_diversity_index`. 

> Shannon entropy is a measure from information theory that quantifies the uncertainty or diversity in a dataset. In the context of energy:
> Higher Entropy: Indicates a more diverse energy mix, with energy production or capacity spread across multiple fuel sources.
> Lower Entropy: Suggests reliance on fewer fuel sources, indicating less diversity.

While both capacity and generation metrics use Shannon entropy, they capture different aspects:
Capacity Entropy: Reflects the potential diversity based on installed infrastructure. It indicates how prepared a state is to utilize various energy sources.   

Generation Entropy: Represents the actual diversity in energy production. It shows how the energy mix is utilized in practice.   

Including both can provide insights into discrepancies between potential and actual energy diversity, which may affect grid resilience and outage durations.

Research suggests that energy systems with higher fuel diversity are more resilient to disruptions. A diverse energy mix can mitigate the impact of outages in specific fuel sources.  
For instance, a study from the University of Texas at Austin analyzed diversity trends in U.S. electricity generation using Shannon entropy and other indices, highlighting the importance of a balanced energy mix for system resilience.


In [11]:
# Form 860
pd.read_csv('existcapacity_annual.csv', skiprows=1).head(2)

Year State Code                              Producer Type  Fuel Source  \
0  1990         AK  Combined Heat and Power, Commercial Power  All Sources   
1  1990         AK  Combined Heat and Power, Commercial Power         Coal   

  Generators Facilities Nameplate Capacity (Megawatts)  \
0        NaN          4                           85.9   
1        NaN          3                           65.5   

  Summer Capacity (Megawatts)  
0                        80.1  
1                        61.1

In [12]:
# Form 923 
pd.read_csv('annual_generation_state.csv', skiprows=1).head(2)

YEAR STATE               TYPE OF PRODUCER ENERGY SOURCE  \
0  1990    AK  Total Electric Power Industry         Total   
1  1990    AK  Total Electric Power Industry          Coal   

  GENERATION (Megawatthours)  
0                  5,599,506  
1                    510,573

In [13]:
capacity = pd.read_csv('existcapacity_annual.csv', skiprows=1)
capacity.columns = ['year', 'state', 'producer type', 'fuel source', 'generators', 'facilities', 'nameplate_capacity', 'summer_capacity']
capacity = capacity[capacity['year'].astype(int) >= 2000]
capacity = capacity[capacity['year'].astype(int) <= 2016]

pop_df = outage[['state', 'year', 'population']].drop_duplicates()
capacity['year'] = capacity['year'].astype('str')
capacity = capacity.merge(pop_df, on=['state', 'year'], how='left')

# capacity['nameplate_capacity'] = capacity['nameplate_capacity'].str.replace(',', '')
# capacity['summer_capacity'] = capacity['summer_capacity'].str.replace(',', '')
# capacity['capacity_per_capita'] = capacity['nameplate_capacity'].astype(float) / capacity['population'].astype(float)
# capacity = capacity[['year', 'state', 'capacity_per_capita']]
# capacity = capacity.reset_index().drop(columns=['index'])
capacity_keys = set(zip(capacity['state'], capacity['year']))
pop_keys = set(zip(pop_df['state'], pop_df['year']))

missing_keys = capacity_keys - pop_keys
print(f"Missing population for {len(missing_keys)} state-year pairs.")

Missing population for 479 state-year pairs.


In [14]:
def compute_shannon_entropy(df, group_cols, value_col, new_col_name):
    df = df.copy()
    df[value_col] = df[value_col].astype(float)
    grouped = df.groupby(group_cols)
    
    entropy_list = []
    for name, group in grouped:
        proportions = group[value_col] / group[value_col].sum()
        entropy = -(proportions * np.log(proportions)).sum()
        entropy_list.append((*name, entropy))
    
    entropy_df = pd.DataFrame(entropy_list, columns=group_cols + [new_col_name])
    return entropy_df

In [15]:
capacity = pd.read_csv('existcapacity_annual.csv', skiprows=1)
capacity.columns = ['year', 'state', 'producer type', 'fuel source', 'generators', 'facilities', 'nameplate_capacity', 'summer_capacity']
capacity = capacity[capacity['year'].astype(int) >= 2000]
capacity = capacity[capacity['year'].astype(int) <= 2016]
capacity = capacity[capacity['fuel source'] == 'All Sources'] 
capacity['nameplate_capacity'] = capacity['nameplate_capacity'].str.replace(',', '')
capacity['summer_capacity'] = capacity['summer_capacity'].str.replace(',', '')
capacity['year'] = capacity['year'].astype('str')

capacity_entropy = compute_shannon_entropy(
    df=capacity,
    group_cols=['state', 'year'],
    value_col='nameplate_capacity',
    new_col_name='capacity_fuel_diversity_index'
)
capacity_entropy

state  year  capacity_fuel_diversity_index
0      AK  2000                       0.970639
1      AK  2001                       0.969751
2      AK  2002                       0.955367
3      AK  2003                       0.882028
4      AK  2004                       0.874298
..    ...   ...                            ...
879    WY  2012                       0.916525
880    WY  2013                       0.914905
881    WY  2014                       0.922541
882    WY  2015                       0.898817
883    WY  2016                       0.907399

[884 rows x 3 columns]

In [16]:
generation = pd.read_csv('annual_generation_state.csv', skiprows=1)
generation.columns = ['year', 'state', 'producer_type', 'fuel_source', 'generation_mwh']
generation = generation.dropna(subset=['generation_mwh'])

generation = generation[generation['year'].astype(int) >= 2000]
generation = generation[generation['year'].astype(int) <= 2016]
generation = generation[generation['fuel_source'] == 'Total']

generation['generation_mwh'] = generation['generation_mwh'].replace(',', '', regex=True).astype(float)
generation['year'] = generation['year'].astype('str')
mask = (generation['fuel_source'].str.lower() != 'total') & (generation['generation_mwh'] > 0)
filtered = generation[mask]

generation_entropy = compute_shannon_entropy(
    df=generation,
    group_cols=['state', 'year'],
    value_col='generation_mwh',
    new_col_name='generation_fuel_diversity_index'
)
generation_entropy


/Users/rebeccachen/.local/share/mamba/envs/dsc80/lib/python3.12/site-packages/pandas/core/arraylike.py:399: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)
/Users/rebeccachen/.local/share/mamba/envs/dsc80/lib/python3.12/site-packages/pandas/core/arraylike.py:399: RuntimeWarning: invalid value encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


state  year  generation_fuel_diversity_index
0      AK  2000                         1.022950
1      AK  2001                         1.020200
2      AK  2002                         1.016209
3      AK  2003                         0.917580
4      AK  2004                         0.911863
..    ...   ...                              ...
879    WY  2012                         0.868176
880    WY  2013                         0.862232
881    WY  2014                         0.876187
882    WY  2015                         0.866723
883    WY  2016                         0.880879

[884 rows x 3 columns]

In [17]:
capacity_entropy.head()

state  year  capacity_fuel_diversity_index
0    AK  2000                       0.970639
1    AK  2001                       0.969751
2    AK  2002                       0.955367
3    AK  2003                       0.882028
4    AK  2004                       0.874298

In [18]:
generation_entropy.head()

state  year  generation_fuel_diversity_index
0    AK  2000                         1.022950
1    AK  2001                         1.020200
2    AK  2002                         1.016209
3    AK  2003                         0.917580
4    AK  2004                         0.911863

### Merging engineered features into outages 

In [19]:
outage.shape

(1534, 21)

In [20]:
merged_outage = outage.copy()
merged_outage = (merged_outage.merge(capacity_entropy, how='left', on=['state', 'year'])
                .merge(generation_entropy, how='left', on=['state', 'year']))
merged_outage.head()

year month state      climate_region anomaly_level climate_cat  \
0  2011     7    MN  East North Central          -0.3      normal   
1  2014     5    MN  East North Central          -0.1      normal   
2  2010    10    MN  East North Central          -1.5        cold   
3  2012     6    MN  East North Central          -0.1      normal   
4  2015     7    MN  East North Central           1.2        warm   

            cause_cat  cause_detail  duration  pc_realgsp_state  ...  \
0      severe weather           NaN    3060.0             51268  ...   
1  intentional attack     vandalism       1.0             53499  ...   
2      severe weather    heavy wind    3000.0             50447  ...   
3      severe weather  thunderstorm    2550.0             51598  ...   
4      severe weather           NaN    1740.0             54431  ...   

   pop_pct_uc  popden_urban  popden_uc  popden_rural  area_pct_urban  \
0       15.28        2279.0     1700.5          18.2            2.14   
1       15.28        2279.0     1700.5          18.2            2.14   
2       15.28        2279.0     1700.5          18.2            2.14   
3       15.28        2279.0     1700.5          18.2            2.14   
4       15.28        2279.0     1700.5          18.2            2.14   

   area_pct_uc  yearly_outage_count_bystate  yearly_avg_duration_bystate  \
0          0.6                            3                  1460.666667   
1          0.6                            2                    30.500000   
2          0.6                            3                  2610.000000   
3          0.6                            1                  2550.000000   
4          0.6                            2                   947.500000   

   capacity_fuel_diversity_index  generation_fuel_diversity_index  
0                       1.045207                         0.978170  
1                       1.065896                         0.999916  
2                       1.032858                         0.969911  
3                       1.049795                         1.013572  
4                       1.072869                         1.004192  

[5 rows x 23 columns]

## Univariate Analysis



### Countplot of climate categories

In [21]:
climate_region_count = outage['climate_region'].value_counts().reset_index()
climate_region_count.columns = ['climate_region', 'count']
climate_region_cntplot = px.bar(climate_region_count, x='count', y='climate_region',
            title='Outage Cause Count by Climate region',
            labels={'climate_region': 'Climate Region', 'count': 'Number of Outages'},
            color='count',  
            #color_discrete_sequence=px.colors.qualitative.Pastel  
             )

climate_region_cntplot.show()


In [22]:
climate_region_cntplot.write_html('../assets/plots/climate_region_cntplot.html', include_plotlyjs='cdn')

Log-scaled duration distribution

In [23]:
outage['duration']

0       3060.0
1          1.0
2       3000.0
3       2550.0
4       1740.0
         ...  
1529     720.0
1530       NaN
1531      59.0
1532     181.0
1533       NaN
Name: duration, Length: 1534, dtype: float64

In [24]:
duration = outage['duration']
duration = pd.to_numeric(duration, errors='coerce').dropna()
duration = duration[duration > 0]  # log can't handle zero or negative

log_duration = np.log10(duration)
df = pd.DataFrame({'log_duration': log_duration})

# Create bins manually
bin_edges = np.linspace(log_duration.min(), log_duration.max(), 30)
df['bin'] = pd.cut(df['log_duration'], bins=bin_edges, include_lowest=True)
# Calculate counts per bin
bin_counts = df['bin'].value_counts().sort_index()
bin_centers = [interval.mid for interval in bin_counts.index]


hist_df = pd.DataFrame({
    'bin_center': bin_centers,
    'count': bin_counts.values
})
total_outages = df['log_duration'].notna().sum()
hist_df['percent'] = (hist_df['count'] / total_outages) * 100

# Human can't read 10k minutes so we convert things
def human_readable(mins):
    if mins < 1: 
        return "0 min"
    if mins >= (7 * 1440): 
        return f"{round(mins / (7 * 1440))} weeks"
    elif mins >= 1440:
        return f"{round(mins / 1440)}d"
    elif mins >= 60:
        return f"{round(mins / 60)}h"
    else:
        return f"{int(round(mins))} min"

hist_df['bin_label'] = [
    f"{human_readable(10**interval.left)} –{human_readable(10**interval.right)}"
    for interval in bin_counts.index
]

tick_vals = hist_df['bin_center']
tick_text = [f"{int(np.expm1(x))}" for x in tick_vals]

log_duration = px.bar(
    hist_df,
    x='bin_label',
    y='percent',
    color='bin_center',
    color_continuous_scale=px.colors.sequential.Blackbody,
    labels={'bin_label': 'Duration Range', 'percent': 'Percent of Outages'},
    title='Log Duration of Outages (Percentage)'
)

log_duration.update_layout(
    plot_bgcolor="#d0d5e6",
    xaxis_title='Duration (minutes, approx)',
    xaxis_tickangle=-45
)

log_duration.update_traces(
    hovertemplate=
        'Duration Range: %{x}<br>' +
        'Percent of Outages: %{y:.2f}%<extra></extra>'
)

log_duration.show()



In [25]:
log_duration.write_html('../assets/plots/log_duration.html', include_plotlyjs='cdn')

#### Cause detail wordcloud 

In [26]:
raw.cause_detail
text = ' '.join(
    raw['cause_detail']
    .dropna()
    .astype(str)
    .str.lower()
    .str.strip()
    .str.replace(r'[^\w\s]', '', regex=True)  # Remove punctuation
    .str.replace(r'\s+', ' ', regex=True)
)
wordcloud = WordCloud(
    # colormap='gnuplot2',
    font_path='Impact',
    colormap='cool',
    width=800,
    height=400,
    background_color='white',
    collocations=False,  # Prevent phrases from being split
    random_state=42 
).generate(text)
wc_array = np.array(wordcloud.to_image())

cause_wordcloud = px.imshow(wc_array)
cause_wordcloud.update_layout(
    title="Word Cloud of Causes of Outages",
    xaxis=dict(showticklabels=False),
    yaxis=dict(showticklabels=False),
    margin=dict(l=10, r=10, t=40, b=10)
)
cause_wordcloud.show()

In [27]:
cause_wordcloud.write_html('../assets/plots/cause_wordcloud.html', include_plotlyjs='cdn')

## Bivariate Analysis

In [28]:
converted_anomaly_level = outage.copy()
converted_anomaly_level['anomaly_level'] = converted_anomaly_level['anomaly_level'].astype(float)

def iqr(x):
    return x.quantile(0.75) - x.quantile(0.25)

state_order = (
    converted_anomaly_level.groupby('state')['anomaly_level']
    .apply(iqr)
    .sort_values()
    .index
)

anomaly_by_state = px.box(
    converted_anomaly_level,
    x='state',
    y='anomaly_level',
    color='state',
    category_orders={'state': state_order},
    title='Anomaly Levels by State',
)


anomaly_by_state.update_layout(
    xaxis_title='State',
    yaxis_title='Anomaly Level',
    title_font=dict(size=30),
    xaxis_tickangle=90,
    font=dict(size=10),
    height=400,
    width=800,
    showlegend=False 
)

anomaly_by_state.show()


/var/folders/q9/dv0qd5v93jv_7gz3d0y5d0xc0000gn/T/ipykernel_41582/1787077911.py:8: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.



In [29]:
anomaly_by_state.write_html('../assets/plots/anomaly_by_state.html', include_plotlyjs='cdn')

In [30]:

agg_df = outage.groupby(['climate_region', 'cause_cat']).size().reset_index(name='outage_count')
agg_df = agg_df.sort_values(['climate_region', 'cause_cat'])

ordered_regions = ['Northeast', 'West North Central', 'Southwest', 'Northwest', 'East North Central', 'Southeast', 'Central', 'West', 'South']

regions = agg_df['climate_region'].unique()
colors = ['#33a8c7ff', '#52e3e1ff', '#a0e426ff', '#fdf148ff', '#ffab00ff',  '#f77976ff', '#f050aeff', '#d883ffff', '#9336fdff' ]
colors2 = ["#ef476f","#f78c6b","#ffd166","#83d483","#06d6a0","#0cb0a9","#118ab2","#0c637f","#073b4c"]
colors3 = ["#5d9cec","#4fc1e9","#48cfad","#a0d468","#ffce54","#fc6e51","#ed5565","#ac92ec","#ec87c0"]
colors4= ["#ff7073","#ea9e8d","#dbb3b1","#ffe085","#fed35d","#96e6b3","#73d3c9","#8cd9f8","#a0b7cf"]
color_map = {region: colors[i % len(colors4)] for i, region in enumerate(ordered_regions)}

climate_cause_pie = px.sunburst(
    agg_df,
    path=['climate_region', 'cause_cat'],  # hierarchy: inner ring is climate_region, outer is cause_cat
    values='outage_count',
    color='climate_region',
    color_discrete_map=color_map,
    #color='outage_count',  
    #color_continuous_scale=px.colors.sequential.Plasma,
    title='Outage Counts by Climate Region and Cause Category'
)
climate_cause_pie.update_layout(width=500, height=500)
climate_cause_pie.update_traces(insidetextorientation='radial') 
climate_cause_pie.show()

/var/folders/q9/dv0qd5v93jv_7gz3d0y5d0xc0000gn/T/ipykernel_41582/1133863440.py:1: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.

/Users/rebeccachen/.local/share/mamba/envs/dsc80/lib/python3.12/site-packages/plotly/express/_core.py:1727: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.

/Users/rebeccachen/.local/share/mamba/envs/dsc80/lib/python3.12/site-packages/plotly/express/_core.py:1727: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence thi

In [31]:
climate_cause_pie.write_html('../assets/plots/climate_cause_pie.html', include_plotlyjs='cdn')

In [32]:
count_heatmap = px.density_heatmap(
    outage,
    x='year',
    y='state',
    z='yearly_outage_count_bystate',
    histfunc='avg',
    color_continuous_scale='Plasma',
    labels={'year': 'Year', 'state': 'State', 'yearly_outage_count_bystate': 'Avg Outage Count'},
    title='Average Yearly Outage Count by State'
)

count_heatmap.update_layout(
    yaxis={'categoryorder':'total ascending'},  # Sort states by total outages ascending
    xaxis=dict(dtick=1), 
    height=800,
    plot_bgcolor='#f0f0f0', 
    font=dict(size=10)
)

count_heatmap.show()


In [33]:
count_heatmap.write_html('../assets/plots/count_heatmap.html', include_plotlyjs='cdn')

In [34]:

raw_to_vis = raw.copy()
raw_to_vis['duration'] = raw_to_vis['duration'].astype(float)
df_month = (
    raw_to_vis.dropna(subset=['duration'])
    .assign(year_month=lambda df: pd.to_datetime(df['year'].astype(str) + '-' + df['month'].astype(str).str.zfill(2)))
    .groupby('year_month', as_index=False)['duration']
    .mean()
    .rename(columns={'year_month': 'time'})
)
df_month['type'] = 'Year-Month'

# Prepare year data
df_year = (
    raw_to_vis.dropna(subset=['duration'])
    .groupby('year', as_index=False)['duration']
    .mean()
    .rename(columns={'year': 'time'})
)
df_year['type'] = 'Year'

# Combine
df_combined = pd.concat([df_month, df_year], ignore_index=True)

scatter = px.scatter(
    raw_to_vis.dropna(subset=['duration'])
    .assign(year_month=lambda df: pd.to_datetime(df['year'].astype(str) + '-' + df['month'].astype(str).str.zfill(2))),
    x='year_month',
    y='duration',
    opacity=0.3,
    labels={'year_month': 'Year-Month', 'duration': 'Duration (min)'},
    title='Outage Durations: Individual Points + Monthly Average'
)

# Plot
avg_outage_duration = px.line(
    df_combined,
    x='time',
    y='duration',
    color='type',
    labels={'time': 'Time', 'duration': 'Avg Outage Duration (minutes)', 'type': 'Aggregation'},
    title='Average Outage Duration: Year-Month and Year',
)

avg_outage_duration.update_layout(height=400)
avg_outage_duration.show()

In [35]:
avg_outage_duration.write_html('../assets/plots/avg_outage_duration.html', include_plotlyjs='cdn')

In [36]:
outage.columns

Index(['year', 'month', 'state', 'climate_region', 'anomaly_level',
       'climate_cat', 'cause_cat', 'cause_detail', 'duration',
       'pc_realgsp_state', 'pi_util_of_usa', 'population', 'pop_pct_urban',
       'pop_pct_uc', 'popden_urban', 'popden_uc', 'popden_rural',
       'area_pct_urban', 'area_pct_uc', 'yearly_outage_count_bystate',
       'yearly_avg_duration_bystate'],
      dtype='object')

### Interesting Aggregates 

In [37]:
df = merged_outage.copy()

threshold = df['capacity_fuel_diversity_index'].median()
df['fuel_diversity_group'] = np.where(
    df['capacity_fuel_diversity_index'] >= threshold, 'High', 'Low'
)
df_pivot = df.dropna(subset=['duration', 'climate_region'])
pivot = pd.pivot_table(
    df_pivot,
    values='duration',
    index='cause_cat',
    columns='climate_cat',
    aggfunc='mean'
)
overall = df_pivot.groupby('climate_cat')['duration'].mean()
pivot.loc['Overall'] = overall
pivot


/var/folders/q9/dv0qd5v93jv_7gz3d0y5d0xc0000gn/T/ipykernel_41582/650177226.py:8: FutureWarning:

The default value of observed=False is deprecated and will change to observed=True in a future version of pandas. Specify observed=False to silence this warning and retain the current behavior

/var/folders/q9/dv0qd5v93jv_7gz3d0y5d0xc0000gn/T/ipykernel_41582/650177226.py:15: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.



climate_cat                            cold       normal          warm
cause_cat                                                             
equipment failure                308.235294  3201.428571    505.000000
fuel supply emergency          17433.000000  7658.823529  22799.666667
intentional attack               497.282051   426.817778    312.557377
islanding                        259.266667   142.176471    209.833333
public appeal                   2125.909091  1376.529412    596.230769
severe weather                  3288.025316  4070.401709   4458.697368
system operability disruption    601.861111   953.589286    478.200000
Overall                         2659.748918  2537.369505   2828.654804

In [38]:
pivot_reset = pivot.reset_index()
heatmap_df = pivot_reset.melt(id_vars='cause_cat', var_name='climate_cat', value_name='avg_duration')
pivot_fig = px.density_heatmap(
    heatmap_df,
    x='climate_cat',
    y='cause_cat',
    z='avg_duration',
    color_continuous_scale='Plasma',
    title='Average Duration Heatmap by Cause Category and Climate Category',
    labels={'avg_duration': 'Avg Outage Duration', 'cause_cat': 'Cause Category', 'climate_cat': 'Climate Category'}
)

pivot_fig.update_layout(yaxis={'categoryorder':'total ascending'})  
pivot_fig.show()

In [39]:
pivot_fig.write_html('../assets/plots/pivot_fig.html', include_plotlyjs='cdn')

In [40]:
def detect_simpsons_paradox(df, X, Y, group_col, min_group_size=10):
    data = df[[X, Y, group_col]].dropna()
    overall_corr = data[X].corr(data[Y])
    group_corrs = {}
    for g, group_df in data.groupby(group_col):
        if len(group_df) >= min_group_size:
            corr = group_df[X].corr(group_df[Y])
            group_corrs[g] = corr
    valid_corrs = {k: v for k, v in group_corrs.items() if not pd.isna(v)}
    if overall_corr == 0 or np.isnan(overall_corr):
        return {
            'overall_corr': overall_corr,
            'group_corrs': valid_corrs,
            'simpsons_paradox': False,
            'message': 'Overall correlation is zero or undefined.'
        }

    overall_sign = np.sign(overall_corr)
    opposite_signs = [np.sign(corr) == -overall_sign for corr in valid_corrs.values()]
    paradox = all(opposite_signs) and len(opposite_signs) > 0

    return {
        'overall_corr': overall_corr,
        'group_corrs': valid_corrs,
        'simpsons_paradox': paradox,
        'message': 'Simpson\'s paradox detected!' if paradox else 'No Simpson\'s paradox detected.'
    }

result = detect_simpsons_paradox(
    df=merged_outage,
    X='capacity_fuel_diversity_index',
    Y='duration',
    group_col='climate_region'
)

print(result['message'])
print('Overall correlation:', result['overall_corr'])
print('Group correlations:', result['group_corrs'])



No Simpson's paradox detected.
Overall correlation: 0.030517313280907593
Group correlations: {'Central': np.float64(0.1657583102434873), 'East North Central': np.float64(-0.05327743519282365), 'Northeast': np.float64(0.08214811823653359), 'Northwest': np.float64(-0.08506823051090759), 'South': np.float64(0.031445524799168616), 'Southeast': np.float64(-0.07575005052507618), 'Southwest': np.float64(0.26832601335900524), 'West': np.float64(0.0489307607752173), 'West North Central': np.float64(-0.39788756473038117)}


/var/folders/q9/dv0qd5v93jv_7gz3d0y5d0xc0000gn/T/ipykernel_41582/2512304999.py:5: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.



# Step 3: Assessment of Missingness
1. Inspect how much missing data there is in each column (percentage) (rename the dataframe to outage, so that there's destintion between raw dataset (used for missingness later) and real dataset we will be using)
2. Decide on how to fill in missingness (drop? mean imputation? probability imputation?)
3. Feature engineer however you think is fit. 

In [41]:
(outage.isna().sum(axis = 0) / outage.shape[0]).sort_values(ascending= False)

cause_detail                   0.307040
duration                       0.037810
yearly_avg_duration_bystate    0.009126
popden_rural                   0.006519
popden_uc                      0.006519
anomaly_level                  0.005867
climate_cat                    0.005867
month                          0.005867
climate_region                 0.003911
popden_urban                   0.000000
yearly_outage_count_bystate    0.000000
area_pct_uc                    0.000000
area_pct_urban                 0.000000
year                           0.000000
pop_pct_uc                     0.000000
pop_pct_urban                  0.000000
population                     0.000000
pc_realgsp_state               0.000000
cause_cat                      0.000000
state                          0.000000
pi_util_of_usa                 0.000000
dtype: float64

### Columns with notably large amounts of missing data:  
demand_loss_mw  
customers_affected  
cause_detail  
hurricane_names  


#### Assessing missingness for duration 

In [42]:
duration_nmar = outage.copy()['duration'].value_counts().reset_index()
duration_nmar['duration'] = duration_nmar['duration'].astype(int)
duration_nmar.sort_values(by = 'duration', ascending = False)

duration  count
620    108653      1
679     78377      1
216     60480      1
368     49427      1
174     49320      2
..        ...    ...
125         4      2
61          3      3
16          2      6
0           1     97
1           0     78

[852 rows x 2 columns]


## NMAR Assessments
### Addressing Missingness of Cause Detail
The missingness of the **cause_detailed** col is most likely NMAR since the details might give sensitive information about an individual. Usually when an outage occurs, we can expect to see a recording or failsafe that indicates what was broken. That said, if the outage occurs in under-resourced areas then there is a much higher chance that it is not recorded at all due to lack of infrastructure.

### Addressing Missingness of Duration
On the other hand, we have reason believe that **duration** not NMAR since even though we can make a case that if a duration is too low or too high it might not be recorded. Why we believe that reasoning is flawed is because the **duration** column has 78 entries that only have 0 duration. Since, duration is non negative and the max duration is rather high, we can say that this missingness cannot be determined by the value within the column itself. If anything, if an outage lasts very long then there is more reason that it should be recorded for record keeping. So it is not NMAR.

<!-- We believe it may be MAR because the duration of an outage can vary based on how the population is concentrated, the cause detail (typhoon or natural disasters more likely to cause much more damage to the infrastructure making it less likely that the equipment to collect the data may be tampered with), month is there is a pattern of months that specifically has many outages that l -->

### Addressing Missingness of Climate Category and Region
It doesn't make much sense to label this as NMAR because all geographical regions in the country are labeled with their respective category and region, so it is unlikely that an outtage would happen in an area that cannot be classified as one of them. Thus, it cannot be that the missingness is dependent on the value of the entry within the coclumn itself. 

### Addressing Missingness of popden_uc, popden_rural
There is no reason to believe that these columns are NMAR since the population level, urban or not, is highly dependent on the state and its population, both of which are features in our data. 

# MAR Testing

It is intriguing to analyze whether the cause_detail missingness is dependent on any other columns within our cleaned dataset.   
Here, we only use average TVD for each categorical column for simplicity. One can further enhance this by calculating TVD for every group of every categorical column.


In [43]:
def mean_diff(x, y):
    if len(x) == 0 or len(y) == 0:
        return 0  # or np.nan, but avoid this
    return np.mean(x) - np.mean(y)

#we are going to go through every combination of rows and 
#calculate the average TVD for that categorical column in outage dataframe
def avg_tvd_categoricals(table): 
    rows = table.index 
    total_tvd = 0
    count = 0
    for i, j, in combinations(rows, 2): # num rows choose 2 amount of combinations
        total_tvd += 0.5*abs(table.loc[i] - table.loc[j]).sum()
        count += 1
    return total_tvd/count

In [44]:
cols = outage.drop(columns = 'cause_detail').columns
mar = {col: 'nothing' for col in cols}
mar_dependent = {}
for col in cols:
    df = outage[[col, 'cause_detail']].copy()
    df['missing'] = df['cause_detail'].isna()
    df['not_missing'] = ~df['missing']
    if is_numeric_dtype(df[col]):
        #using the sample mean as tvd
        missing = df[df['missing'] == True][col].dropna()
        not_missing = df[df['missing'] == False][col].dropna()
        result = permutation_test((missing, not_missing), statistic = mean_diff,
                                  n_resamples = 2000, alternative = 'two-sided')
        mar[col] = (True, result.statistic, result.null_distribution, result.pvalue) if result.pvalue < 0.05 else (False, result.statistic, result.null_distribution, result.pvalue)
    else:
        cause_dist = df.pivot_table(index = col, columns = 'missing', aggfunc = 'size', observed = False)
        cause_dist.columns = ['missing', 'not_missing']
        cause_dist = cause_dist / cause_dist.sum()
        obs = cause_dist.diff(axis=1).iloc[:, -1].abs().sum() / 2
        shuffle = df.copy()
        tvd = []
        for i in range(2000):
            shuffle[col] = np.random.permutation(shuffle[col])
            pivoted = (shuffle.pivot_table(index = col, columns = 'missing', aggfunc = 'size', observed = False))
            pivoted = pivoted / pivoted.sum()
            tvd.append(pivoted.diff(axis=1).iloc[:, -1].abs().sum() / 2)
        mar[col] = (True if np.mean(obs > np.array(tvd)) < 0.05 else False, obs, tvd, np.mean(obs > np.array(tvd)))
    if mar[col][0]:
        mar_dependent[col] = mar[col]

In [45]:
def plot_test_histogram(tupl, col_name, nbins=50):
    null = tupl[2]
    stat = tupl[1]
    col = col_name
    pval = tupl[3]

    fig = px.histogram(
        x=null, 
        nbins=nbins, 
        histnorm='probability',
        title=f'Null Distribution for {col} (p = {pval:.3f})', 
    )
    fig.add_vline(
        x=stat, 
        line_color='red', 
        line_width=2,
        annotation_text=f"Observed = {stat:.3f}",
        annotation_position="top right"
    )
    fig.update_layout(
        xaxis_title="Test Statistic",
        yaxis_title="Probability",
        showlegend=False
    )
    fig.update_traces(
    marker_line_color='white',  # bar border color
    marker_line_width=1.5       # bar border width
)
    fig.show()
    return fig 

In [46]:
mar_yearly_avg_duration = plot_test_histogram(mar_dependent['yearly_avg_duration_bystate'],'yearly_avg_duration_bystate', nbins=50)

In [47]:
mar_yearly_avg_duration.write_html('../assets/plots/mar_yearly_avg_duration.html', include_plotlyjs='cdn')

In [48]:
mar_pc_realgsp = plot_test_histogram(mar['pc_realgsp_state'],'pc_realgsp_state',nbins=50)

In [49]:
mar_pc_realgsp.write_html('../assets/plots/mar_pc_realgsp.html', include_plotlyjs='cdn')

In [50]:
for key in list(mar_dependent.keys()):
    print(str(key) + " and p-value is " + str(mar_dependent[key][3]))

pi_util_of_usa and p-value is 0.0009995002498750624
population and p-value is 0.0009995002498750624
pop_pct_urban and p-value is 0.0029985007496251873
popden_urban and p-value is 0.0009995002498750624
popden_uc and p-value is 0.0009995002498750624
popden_rural and p-value is 0.0009995002498750624
area_pct_urban and p-value is 0.0009995002498750624
area_pct_uc and p-value is 0.0009995002498750624
yearly_outage_count_bystate and p-value is 0.0009995002498750624
yearly_avg_duration_bystate and p-value is 0.029985007496251874


In [51]:
print(list(mar_dependent.keys()))

['pi_util_of_usa', 'population', 'pop_pct_urban', 'popden_urban', 'popden_uc', 'popden_rural', 'area_pct_urban', 'area_pct_uc', 'yearly_outage_count_bystate', 'yearly_avg_duration_bystate']


It seems that the missingness of cause_detail is dependent on 11 out of 21 columns: ['pi_util_of_usa', 'population', 'pop_pct_urban', 'popden_urban', 'popden_uc', 'popden_rural', 'area_pct_urban', 'area_pct_uc', 'monthly_outage_count_bystate', 'monthy_avg_duration_bystate']. 

In [52]:
def plot_distribution_by_missingness(df, col, target='cause_detail', nbins=50):
    df = df[[col, target]].copy()
    df['missing'] = df[target].isna()

    if is_numeric_dtype(df[col]):
        df = df.dropna(subset=[col])
        
        min_val = df[col].min()
        max_val = df[col].max()
        bin_size = (max_val - min_val) / nbins

        fig = go.Figure()
        

        for missing_status in [True, False]:
            subset = df[df['missing'] == missing_status]
            fig.add_trace(go.Histogram(
                x=subset[col],
                name=f"{'Missing' if missing_status else 'Not Missing'}",
                opacity=0.6,
                histnorm='probability',
                xbins=dict(start=min_val, end=max_val, size=bin_size)
            ))

        fig.update_layout(
            barmode='overlay',
            title=f'Distribution of {col} by Missingness in {target}',
            xaxis_title=col,
            yaxis_title='Probability',
        )
        fig.update_traces(
            marker_line_color='white',  # bar border color
            marker_line_width=1.5       # bar border width
        )
        fig.show()
        return fig
    else:
        count_df = df.groupby([col, 'missing']).size().reset_index(name='count')
        fig = px.bar(
            count_df,
            x=col,
            y='count',
            color='missing',
            barmode='group',
            title=f'Counts of {col} by Missingness in {target}',
            labels={'missing': 'Cause Detail Missing'}
        )
        fig.update_layout(xaxis_title=col, yaxis_title='Count')
        fig.show()
        return fig 


In [53]:
yearly_avg_duration_distribution = plot_distribution_by_missingness(outage, 'yearly_avg_duration_bystate')


In [54]:
yearly_avg_duration_distribution.write_html('../assets/plots/yearly_avg_duration_distribution.html', include_plotlyjs='cdn')

In [55]:
pc_realgsp_distribution = plot_distribution_by_missingness(outage, 'pc_realgsp_state')


In [56]:
pc_realgsp_distribution.write_html('../assets/plots/pc_realgsp_distribution.html', include_plotlyjs='cdn')

# Step 4: Hypothesis testing
Recall our problem statement:   
**Assessment of Infrastructure Resilience (Based on whether or not cause_detail has enough information.) Analyze how different regions' infrastructure <u>*maintenance investments*</u> correlate with outage frequency and duration. This can inform infrastructure improvement strategies, based on yearly spent on utility for each state**

### Requirements: 
1. Clearly state a pair of hypotheses and perform a hypothesis test or permutation test that is not related to missingness. 
2. Clearly state your null and alternative hypotheses, your choice of test statistic and significance level, the resulting 
p -value, and your conclusion. Justify why these choices are good choices for answering the question you are trying to answer.

Optional: Embed a visualization related to your hypothesis test in your website.

Tip: When making writing your conclusions to the statistical tests in this project, never use language that implies an absolute conclusion; since we are performing statistical tests and not randomized controlled trials, we cannot prove that either hypothesis is 100% true or false.

**H₀ (null): There is no difference in average outage duration between states with high and low fuel diversity.   
H₁ (alt): States with higher fuel diversity have shorter average outage durations.**

In [57]:
df = merged_outage.copy()
threshold = df['capacity_fuel_diversity_index'].median()
high_div = df[df['capacity_fuel_diversity_index'] >= threshold]['duration'].dropna().values
low_div = df[df['capacity_fuel_diversity_index'] < threshold]['duration'].dropna().values

obs_diff = np.mean(high_div) - np.mean(low_div)

n_iterations = 100000
diffs = []

for _ in range(n_iterations):
    sample_high = np.random.choice(high_div, size=len(high_div), replace=True)
    sample_low = np.random.choice(low_div, size=len(low_div), replace=True)
    diff = np.mean(sample_high) - np.mean(sample_low)
    diffs.append(diff)

diffs = np.array(diffs)
p_val = np.mean(np.abs(diffs) >= np.abs(obs_diff))

print(f'Observed Difference: {obs_diff:.3f}')
print(f'Bootstrap p-value: {p_val:.3f}')


Observed Difference: 600.452
Bootstrap p-value: 0.502


In [58]:
ht_capacity = px.histogram(
    x=diffs,
    nbins=50,
    histnorm='probability',
    title=f'Distribution of Mean Differences: Capacity Fuel Diversity Index <br>(Observed = {obs_diff:.2f}, p = {p_val:.3f})',
    labels={'x': 'Mean Difference', 'y': 'Probability'},
    opacity=0.75
)

ht_capacity.add_vline(
    x=obs_diff,
    line_color='red',
    line_width=2,
    annotation_text='Observed Diff',
    annotation_position='top right'
)

ht_capacity.update_layout(
    xaxis_title="Difference in Mean Duration (High - Low Diversity)",
    yaxis_title="Probability",
    bargap=0.05
)

ht_capacity.show()

In [59]:
ht_capacity.write_html('../assets/plots/ht_capacity.html', include_plotlyjs='cdn')

In [60]:
df = merged_outage.copy()
threshold = df['generation_fuel_diversity_index'].median()
high_div = df[df['generation_fuel_diversity_index'] >= threshold]['duration'].dropna().values
low_div = df[df['generation_fuel_diversity_index'] < threshold]['duration'].dropna().values

# Step 2: Observed difference in means
obs_diff = np.mean(high_div) - np.mean(low_div)

# Step 3: Bootstrap
n_iterations = 100000
diffs = []

for _ in range(n_iterations):
    sample_high = np.random.choice(high_div, size=len(high_div), replace=True)
    sample_low = np.random.choice(low_div, size=len(low_div), replace=True)
    diff = np.mean(sample_high) - np.mean(sample_low)
    diffs.append(diff)

# Step 4: P-value (two-tailed)
diffs = np.array(diffs)
p_val = np.mean(np.abs(diffs) >= np.abs(obs_diff))

print(f'Observed Difference: {obs_diff:.3f}')
print(f'Bootstrap p-value: {p_val:.3f}')


Observed Difference: 419.587
Bootstrap p-value: 0.490


In [61]:
ht_generated = px.histogram(
    x=diffs,
    nbins=50,
    histnorm='probability',
    title=f'Bootstrap Distribution of Mean Differences: Generated Fuel Diversity Index<br>(Observed = {obs_diff:.2f}, p = {p_val:.3f})',
    labels={'x': 'Mean Difference', 'y': 'Probability'},
    opacity=0.75
)

ht_generated.add_vline(
    x=obs_diff,
    line_color='red',
    line_width=2,
    annotation_text='Observed Diff',
    annotation_position='top right'
)

ht_generated.update_layout(
    xaxis_title="Difference in Mean Duration (High - Low Diversity)",
    yaxis_title="Probability",
    bargap=0.05
)

ht_generated.show()

In [62]:
ht_generated.write_html('../assets/plots/ht_generated.html', include_plotlyjs='cdn')

In [63]:
outage_counts = outage.groupby(['state', 'year']).size().reset_index(name='outage_count')
merged = outage_counts.merge(capacity_entropy, on=['state', 'year'], how='left')

threshold = merged['capacity_fuel_diversity_index'].median()
high_div = merged[merged['capacity_fuel_diversity_index'] >= threshold]['outage_count'].values
low_div = merged[merged['capacity_fuel_diversity_index'] < threshold]['outage_count'].values
obs_diff = np.mean(high_div) - np.mean(low_div)

n_iterations = 10000
diffs = []
for _ in range(n_iterations):
    sample_high = np.random.choice(high_div, size=len(high_div), replace=True)
    sample_low = np.random.choice(low_div, size=len(low_div), replace=True)
    diffs.append(np.mean(sample_high) - np.mean(sample_low))

p_val = np.mean(np.array(diffs) <= obs_diff) 
p_val

/var/folders/q9/dv0qd5v93jv_7gz3d0y5d0xc0000gn/T/ipykernel_41582/245067319.py:1: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.



np.float64(0.4921)

In [64]:
outage_counts = outage.groupby(['state', 'year']).size().reset_index(name='outage_count')
merged = outage_counts.merge(capacity_entropy, on=['state', 'year'], how='left')

threshold = merged['capacity_fuel_diversity_index'].median()
high_div = merged[merged['capacity_fuel_diversity_index'] >= threshold]['outage_count'].values
low_div = merged[merged['capacity_fuel_diversity_index'] < threshold]['outage_count'].values
obs_diff = np.mean(high_div) - np.mean(low_div)

n_iterations = 10000
diffs = []
for _ in range(n_iterations):
    sample_high = np.random.choice(high_div, size=len(high_div), replace=True)
    sample_low = np.random.choice(low_div, size=len(low_div), replace=True)
    diffs.append(np.mean(sample_high) - np.mean(sample_low))

p_val = np.mean(np.array(diffs) <= obs_diff)  
p_val

/var/folders/q9/dv0qd5v93jv_7gz3d0y5d0xc0000gn/T/ipykernel_41582/3717411209.py:1: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.



np.float64(0.4967)

# Step 5: Model
To get a closer look into the relationship between our features and outage duration, we have decided to make our task be about predicting the average outage duration per state per year through regression. By predicting this response variable, we aim to provide a model that can derive average outage duration data catered to each state to more accurately. We will propose a baseline model, starting with linear regression, as it is one of the simpler models, with percent RMSE, the percentage of RMSE over the mean of the average duration per state per year feature.

Our features of interest include `climate_region`, `cause_cat`, `population`, `capacity_fuel_diversity_index`, and `generation_fuel_diversity_index`. These features are either fixed (e.g., geographic or categorical labels) or collected prior to the prediction year through public data sources, ensuring they would be available at the time of prediction. This respects the temporal constraint of not using information from after the event we aim to predict.

Understanding the causes and characteristics of major power outages is more critical than ever in today’s climate-challenged and energy-dependent world. Our dataset combines detailed records of U.S. outage events with regional economic, environmental, and energy generation data, offering a rare opportunity to explore how infrastructure resilience varies across states.
By building a model to predict average outage duration based on interpretable features that are known ahead of time, our project aims to offer a small but practical step toward using data to better understand grid reliability.

# Step 6: Baseline model
First, we tried to use Linear Regression alone with all other covariates to predict the average duration of outages per year per state, but it was not fruitful as the RMSE was too high. This can be explained due to the nature of our testing set. As much as the model can learn from the training dataset with all the covariates in its hands, if it does not perform much worse than the training with the testing dataset, then we can consider it a good model. This is because it has shown some robustness against new, and possibly independent, data from outside the one it was trained from.

However, we were suspicious of our findings, and so we looked further into how further test our model's predictive power. We came across Dummy Regression where our model would try to fit a constant line and failed. So then, we can conclude that the model we have is not great at predicting.

So we looked towards Random Tree Regression which is more forgiving when it comes to non-linear trends in our data that the linear regression. However, we only used 'climate_region',
       'cause_cat', 'population',
       'capacity_fuel_diversity_index', 'generation_fuel_diversity_index' to predict average outage duration for each state per year. RF MSE: 4983457.59

We can improve by choosing more variables to work with and let the RFG optimize based on that. We also want to be able to choose optimal hyperparameters in the form of tree depth and amount of trees to produce in order to find a balance between the bias and variance trade off. What we did here with RF was just not restricting its depth which can make it less optimal when getting prediction error.

Analysis on model:
+ Cause category and climate region (both are nominal as they do not have an apparent ordering) both are intuitively related to the duration of outages since they directly play into the reason for the outage occuring in the first place. So, it makes sense to include them to see if they have any contributions to predicting average duration. Both of them are going to be one hot encoded
+ For population (quantitative), it is important to tell how much electricity is being distributed to each household on average and interesting to see if this is indeed something closely related to average outage duration. 
+ capacity_fuel_diversity_index and generation_fuel_diversity_index are there to tell us information on the efficiency and supply of electricity. 

In [65]:


#merged_outage = merged_outage.drop(columns = ['cause_detail'])
model_df = merged_outage[['climate_region',
       'cause_cat', 'population', 'yearly_avg_duration_bystate',
       'capacity_fuel_diversity_index', 'generation_fuel_diversity_index']]
X = model_df.dropna().drop(columns = 'yearly_avg_duration_bystate')
y = model_df.dropna()['yearly_avg_duration_bystate']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# 1. categorical columns
categorical = ['climate_region', 'cause_cat']
numerical = [col for col in X.columns if col not in categorical]

# 2. preprocessor
preprocessor = ColumnTransformer(
    [
        ('scaler', StandardScaler(), numerical),
        ('onehot', OneHotEncoder(sparse_output=False, handle_unknown='ignore'), categorical)
    ],
    remainder='drop'
)

# 3. pipeline
pipeline = make_pipeline(
    preprocessor,
    LinearRegression()
)

# 6. Fit the model
pipeline.fit(X_train, y_train)
y_pred = pipeline.predict(X_test)
# 7. Evaluate
r2 = r2_score(y_test, y_pred)
print(f"R² Score: {r2:.3f}")
mse = mean_squared_error(y_test, pipeline.predict(X_test))
print(f"Test MSE for baseline LR model: {mse:.2f}")
print("RMSE for baseline LR model: " + str(np.sqrt(mse) / np.mean(y) * 100))

rf_model = RandomForestRegressor(
    n_estimators=2000,  # more trees
    max_depth=None,    # allow full growth
    random_state=42,
    n_jobs=-1          # use all cores
)

pipeline_rf = make_pipeline(preprocessor, rf_model)
pipeline_rf.fit(X_train, y_train)

# Get feature names after preprocessing
# This requires sklearn >= 1.0
ohe_columns = pipeline_rf.named_steps['columntransformer'].named_transformers_['onehot'].get_feature_names_out(categorical)
all_feature_names = numerical + list(ohe_columns)

y_pred_rf = pipeline_rf.predict(X_test)
mse_rf = mean_squared_error(y_test, y_pred_rf)
r2 = r2_score(y_test, y_pred_rf)
print(f"R² Score: {r2:.3f}")
print(f"RF MSE: {mse_rf:.2f}")
print("RMSE for baseline RF model: " + str(np.sqrt(mse_rf) / np.mean(y) * 100))


R² Score: 0.104
Test MSE for baseline LR model: 8455566.45
RMSE for baseline LR model: 111.28294913140468
R² Score: 0.470
RF MSE: 4996551.57
RMSE for baseline RF model: 85.54457245365353


In [66]:
((2235.2967521114506 -  2166.9378956680084) / 2235.2967521114506) *100

3.0581557629371003

# Step 7: Final model

In order to narrow down which features to use, we will analyze multicollinearity to rule out columns that may not contribute much to our model given the features that are already in it.

We sense that there is a strong multicollinearity pattern among the columns that are related to population, for example:

['population', 'pop_pct_urban', 'pop_pct_uc',
       'popden_urban', 'popden_uc', 'popden_rural', 'area_pct_urban',
       'area_pct_uc']

This is to be expected since they all, in one way or another tie back to the population of their respective states. This means that they are dependent columns and this introduces multicollinearity. That is to say, since we already have the population feature in our model, there isn't a need to include these other population-based features.

Other notable multicollinearity occurrences are between the Shannon Entropy columns against the columns in our original dataframe that correspond to geographical elements (i.e. not anomaly level, duration, avergae duration, or pc_realgsp_state)

So, it might not be the best idea to use geographical elements along with the capacity and generation indeces.

Despite us showing you which columns have high correlation with one another, it is important to focus on the main objective with our model, **prediction**. And so, since multicollinearity does not affect our prediction power, only the statistical significance of the covariates, we need not worry about it for now. Although, it would be interesting to see.

We would like to one hot encode the state column to see if there are any states that have have a say in the average duration of outages. Based on our EDA, it would seem that this may be the case due to the sheer amount of outages happening in some states. For example CA, TX, and WA have yearly outage count of over 20.

Proposition

Since **Random Forest Regression** shows promise in the baseline model, performing a lot better than Linear Regression, we will choose to use it here for our model refinement. Through GridSearch cross validation, we hope to fine tune its hyperparameters (depth for overfitting, number of trees for variance reduction)

Here's what tuning hyperparameters can do for us:

+ Each decision tree in the forest is trained on a random sample with replacement of the training data.

+ This sampling introduces diversity among the trees which is to say the trees are less dependent on each other and reduces bias.

+ The model then averages the predictions from all trees, which reduces variance of the ensemble (by the law of large numbers).

So we have decided to tune on the following hyperparameters:
| Hyperparameter      | What it Affects                                                        |
| ------------------- | ---------------------------------------------------------------------- |
| `n_estimators`   (int)      | More trees generally reduce variance, but take longer                  |
| `max_depth`   (int)         | Limits complexity; larger values may overfit                           |
| `max_features`   (int)      | Controls the randomness of splits; smaller values = more diverse trees |
| `bootstrap`   (boolean)         | Enables bootstrapping (random sampling with replacement)               |

In [67]:
# covariance_matrix = merged_outage.drop(columns = ['year', 'state', 'climate_region', 'climate_cat',
#        'cause_cat']).corr()
# plt.figure(figsize=(12, 8))
# sns.heatmap(covariance_matrix, annot=True, cmap='coolwarm', mask=np.tril(covariance_matrix, k=-1))
# covariance_matrix = model_df.drop(columns = categorical).corr()
# plt.figure(figsize=(12, 8))
# sns.heatmap(covariance_matrix, annot=True, cmap='coolwarm', mask=np.tril(covariance_matrix, k=-1))
param_grid = {
        'randomforestregressor__n_estimators': [200, 500, 1000, 1500],
        'randomforestregressor__max_depth': [10, 30, 50, 70, None],
        'randomforestregressor__max_features': ['sqrt'],
        'randomforestregressor__bootstrap': [True, False]
    }
X_train = pd.concat([X_train, merged_outage.loc[X_train.index, ['state']]], axis = 1)
X_test = pd.concat([X_test, merged_outage.loc[X_test.index, ['state']]], axis = 1)
pipeline_rf = make_pipeline(preprocessor, RandomForestRegressor(random_state=42, n_jobs=-1))
grid_search = GridSearchCV(
    pipeline_rf,
    param_grid=param_grid,
    cv=10,
    scoring='neg_mean_squared_error',
    n_jobs=-1,
    verbose=2
)

grid_search.fit(X_train, y_train)
y_pred_grid = grid_search.predict(X_test)
rmse = np.sqrt(mean_squared_error(y_test, y_pred_grid))
r2_rf = r2_score(y_test, y_pred_rf)
print("Best parameters found:", grid_search.best_params_)
print("GridSearchCV RMSE on test set:", rmse)
print("So our model's percent RMSE now is ", rmse / np.mean(y) * 100)
print("This is a " + str(85.43240972763235*100/83.82504036536093 - 100) + "% improvement from the baseline RF regression model"
" in terms of percent RMSE and the MSE has improved by 3.7275%")
print(f"R² Score: {r2_rf:.3f}, this is a 0.002 improvement")

Fitting 10 folds for each of 40 candidates, totalling 400 fits
[CV] END randomforestregressor__bootstrap=True, randomforestregressor__max_depth=10, randomforestregressor__max_features=sqrt, randomforestregressor__n_estimators=200; total time=   0.4s
[CV] END randomforestregressor__bootstrap=True, randomforestregressor__max_depth=10, randomforestregressor__max_features=sqrt, randomforestregressor__n_estimators=200; total time=   0.4s
[CV] END randomforestregressor__bootstrap=True, randomforestregressor__max_depth=10, randomforestregressor__max_features=sqrt, randomforestregressor__n_estimators=200; total time=   0.4s
[CV] END randomforestregressor__bootstrap=True, randomforestregressor__max_depth=10, randomforestregressor__max_features=sqrt, randomforestregressor__n_estimators=200; total time=   0.4s
[CV] END randomforestregressor__bootstrap=True, randomforestregressor__max_depth=10, randomforestregressor__max_features=sqrt, randomforestregressor__n_estimators=200; total time=   0.4s
[C

In [68]:
# Compute correlation matrix
cov_matrix = merged_outage.drop(columns=[
    'year', 'state', 'climate_region', 'climate_cat',
    'cause_cat', 'cause_detail'
]).corr()

# Mask lower triangle
mask = np.tril(np.ones(cov_matrix.shape)).astype(bool)
cov_matrix_masked = cov_matrix.mask(mask)

# Plot using Plotly
covariance_heatmap = px.imshow(
    cov_matrix_masked,
    text_auto=True,
    color_continuous_scale='RdBu',
    zmin=-1,
    zmax=1,
    title='Upper-Triangle Correlation Heatmap',
    width=1000,
    height=800
)
covariance_heatmap.update_layout(
    autosize=False,
    margin=dict(l=60, r=60, t=60, b=60)
)


In [69]:
covariance_heatmap.write_html('../assets/plots/covariance_heatmap.html', include_plotlyjs='cdn')

## Step 8: Fairness analysis 


To assess model fairness, we choose group the cause category by severe weather or no severe weather. Since our model focuses on average duration based on the predictive power of population, geographical, and energy generation/storage factors, we want to know if the model is actually performing well on severe weather or not. This is an interesting way to answer the question of "How good is the model in identifying natural causes and appropriate assign weights to those causes so that it is predicting average duration fairly?". We will see whether or not our model is robust under why the outage happened. 

it is fitting to test whether or not the model performs well on different groups of climate categories. Specifically, we want to see if the average outage duration is well modeled on severe weather and no severe weather in hopes to bring up awareness of risks that come with outages.

In [73]:
X_test['severe_weather'] = X_test['cause_cat'] == 'severe weather'
testing_df = pd.concat([X_test, y_test], axis = 1)
fairness_result = permutation_test((testing_df[testing_df['severe_weather'] == True]['yearly_avg_duration_bystate'], 
                  testing_df[testing_df['severe_weather'] == False]['yearly_avg_duration_bystate']),
                statistic = mean_diff, n_resamples = 500, alternative = 'two-sided')

# Extract data
observed_stat = fairness_result.statistic
null_distribution = fairness_result.null_distribution

# Create histogram
fairness = go.Figure()

fairness.add_trace(go.Histogram(
    x=null_distribution,
    nbinsx=50,
    # marker=dict(color='blue'),
    name='Null Distribution',
    opacity=0.75
))

# Add red dashed line for observed stat
fairness.add_trace(go.Scatter(
    x=[observed_stat, observed_stat],
    y=[0, max(np.histogram(null_distribution, bins=50)[0])],
    mode='lines',
    line=dict(color='red', dash='dash', width=2),
    name=f'Observed Stat = {observed_stat:.3f}'
))

# Update layout
fairness.update_layout(
    title='Fairness analysis on "sever weather" cause catagory',
    xaxis_title='Mean Difference',
    yaxis_title='Frequency',
    barmode='overlay',
    showlegend=True,
    bargap=0.05
)

fairness.show()


In [74]:
p_value = fairness_result.pvalue
p_value

np.float64(0.003992015968063872)

In [75]:
fairness.write_html('../assets/plots/fairness.html', include_plotlyjs='cdn')